In [1]:
import pandas as pd
from sklearn.linear_model import LinearRegression
from sklearn.cross_validation import cross_val_score, ShuffleSplit
import numpy as np
from itertools import combinations
import statsmodels.api as sm
from statsmodels.stats.outliers_influence import variance_inflation_factor
import time
import matplotlib.pyplot as plt
%matplotlib inline

c:\users\tim\anaconda3\lib\site-packages\sklearn\cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
def import_data(experimental_file, response_file, response):
    'imports data'
    'experimental_file = experimental design csv filename i.e experimental.csv'
    'response_file = results csv filename i.e Response.csv'
    'response = reponse name: i.e rheomix final deg time min or rheomix stability time min'
    
    experimental_df = pd.read_csv(experimental_file)
    response_df = pd.read_csv(response_file)
    
    X = experimental_df[experimental_df.columns.values.tolist()[1:]].values
    y = response_df[response].values
    max1 = max(y)
    min1 = min(y)

    y_norm = [2*((i-min1)/(max1-min1)) - 1 for i in y]
    
    
    X_linear = X
    linear_terms = experimental_df.columns.values.tolist()[1:]
    
    return y_norm, X_linear, linear_terms, experimental_df, response_df
    

In [3]:
def X_gen(model, X_linear):

    for i, j in enumerate(model):
        
        if i == 0 and len(j) == 2: 
            X_new = X_linear[:, model[0][1]]
        
        else:
            
            if len(j) == 2:
                add = X_linear[:, j[1]]

            if len(j) == 3:
                add = X_linear[:, j[1]]*X_linear[:, j[2]]

            X_new2 = np.column_stack((X_new, add))
            X_new = X_new2

    
    return X_new

In [4]:
start = time.time()


# linear_terms = experimental_df.columns.values.tolist()[1:]



def fit_model(experimental_file, response_file, response, AIC_lim, CN_lim):
    

    total_subset = []
    model_subset = []
    
    y, X_linear, linear_terms, experimental_df, response_df = import_data(experimental_file, response_file, response)
    y1 = np.array(y)
    lin_terms = []
    AIC_prev = 1000

    for i in range(len(linear_terms)):
        term = linear_terms[i]
        key = i
        lin_terms.append([term, i])

    cnt = 0
    for i in range(len(lin_terms)):
        for j in combinations(lin_terms, i+1):
            linear_terms = list(j)


            model = [a for a in linear_terms]
            cnt+=1

            X = X_gen(model, X_linear)

            model_fit = sm.OLS(y, X)
            results = model_fit.fit()
            AIC_cur = results.aic
            
            if len(model) == 1:
                
                X1 = X.reshape(len(X), 1)
                model_obj = LinearRegression(fit_intercept=False)
                my_cv = ShuffleSplit(len(y1), n_iter=10, test_size=0.333, random_state=0)

                score = cross_val_score(model_obj, X1, y1, cv=my_cv)                
            
            else:
            
                model_obj = LinearRegression(fit_intercept=False)
                my_cv = ShuffleSplit(len(y1), n_iter=10, test_size=0.333, random_state=0)

                score = cross_val_score(model_obj, X, y1, cv=my_cv)

            
            model_name = '--'
            for i in model:
                
                model_name += i[0] + "--"

            dictionary = {'AIC': results.aic, 'Cond_No': results.condition_number, 'Model': model_name,
                          'r2': results.rsquared, 'No_terms': len(model), 'Kfold': sum(score)/len(score)}
            total_subset.append(dictionary)
            
            if AIC_cur < AIC_lim:
                if results.condition_number < CN_lim:
                    
                    variables = model_fit.exog
                    
                    if len(model) != 1:

                        vif = [variance_inflation_factor(variables, i) for i in range(variables.shape[1])]
                        vif_max = max(vif)

                    else:
                        vif_max = 0


                    if max(vif) < 40:
                        dictionary = {'AIC': results.aic, 'Cond_No': results.condition_number, 'Model': model,
                        'r2': results.rsquared, 'No_terms': len(model), 'VIF': vif_max, 'Kfold': sum(score)/len(score)}
                        
                        model_subset.append(dictionary)

                    
                    
            if AIC_cur < AIC_prev:

                AIC_prev = AIC_cur
                final_model = [model, results, AIC_cur]
                




            poss_terms = []
            for i in range(len(linear_terms)):
                for j in range(len(linear_terms)): 
                    if i < j:
                        poss_terms.append([linear_terms[i][0] + '*' + linear_terms[j][0],  linear_terms[i][1], linear_terms[j][1]])



            for m in range(1, len(poss_terms) + 1):
                for k in combinations(poss_terms, m):

                    model = [a for a in linear_terms]
                    for i in range(m):
                        model.append(k[i])

                    cnt +=1
                    X = X_gen(model, X_linear)

                    model_fit = sm.OLS(y, X)
                    results = model_fit.fit()
                    AIC_cur = results.aic
                    
                    model_obj = LinearRegression(fit_intercept=False)
                    my_cv = ShuffleSplit(len(y1), n_iter=10, test_size=0.333, random_state=0)
                    
                    score = cross_val_score(model_obj, X, y1, cv=my_cv)
                    
                    
                    model_name = '--'
                    for i in model:

                        model_name += i[0] + "--"
                    
                    dictionary = {'AIC': results.aic, 'Cond_No': results.condition_number, 'Model': model_name,
                                  'r2': results.rsquared, 'No_terms': len(model), 'Kfold': sum(score)/len(score)}
                    
                    total_subset.append(dictionary)



                    if AIC_cur < AIC_lim:
                        if results.condition_number < CN_lim:

                            variables = model_fit.exog
                            
                            if len(model) != 1:

                                vif = [variance_inflation_factor(variables, i) for i in range(variables.shape[1])]
                                vif_max = max(vif)

                            else:
                                vif_max = 0


                            if max(vif) < 40:
                                dictionary = {'AIC': results.aic, 'Cond_No': results.condition_number, 'Model': model,
                                'r2': results.rsquared, 'No_terms': len(model), 'VIF': vif_max, 'Kfold': sum(score)/len(score)}
                                
                                model_subset.append(dictionary)


                    if AIC_cur < AIC_prev:
                        
                        AIC_prev = AIC_cur
                        final_model = [model, results, AIC_cur]




    return final_model, total_subset, model_subset


In [5]:
experimental_file = 'experimental.csv'
response_file = 'Response.csv'


test1 = 'rheomix final deg time min'
test2 = 'rheomix stability time min'
response = test1

AIC_lim = 20
CN_lim = 600


final_model, total_subset, model_subset = fit_model(experimental_file, response_file, response, AIC_lim, CN_lim)

[-0.07518123  0.04066424  0.00595714 -0.16237592 -0.21614333  0.09893138
 -0.2452233   0.02890718  0.06835195  0.03758229] [['Xpvc', 0]]
[-0.05665273 -0.24092534 -0.14585932 -0.95454911 -3.20570297 -0.86974859
 -1.87970709 -0.03799819  0.02867522 -1.30201455] [['Xfiller', 1]]
[-0.57515999 -0.71887221 -0.40171308 -1.0530968  -2.25430351 -1.09211295
 -1.36071574 -0.36741406 -0.66486609 -1.17074207] [['Xfr', 2]]
[-0.37080128 -0.12605969 -0.21361922 -1.49407327 -1.0477946  -0.23973553
 -1.11547731 -0.2610384   0.11285619 -0.85952203] [['Xstabiliser', 3]]
[-0.67173981 -0.70208221 -0.65447151 -0.98371891 -1.22735431 -0.57409217
 -1.29020521 -0.59158011 -0.52590965 -1.16466177] [['Xdinp', 4]]
[-0.84411323 -1.01356148 -1.12292237 -2.37833566 -3.59733316 -0.66127563
 -2.59064566 -1.23878021 -0.6544164  -1.71194155] [['Xldh', 5]]
[-1.00014419 -0.59635131 -0.37607724 -1.01235419 -1.90924827 -0.56716167
 -1.24445957 -0.13944935 -0.63929196 -1.64321513] [['Xsph', 6]]
[ 0.05828399  0.12315815  0.101

[ 0.1557765   0.12619234  0.13105746 -0.31143771 -1.3704854   0.03190495
 -0.45059688  0.14243626  0.14210445  0.15779706] [['Xpvc', 0], ['Xfiller', 1], ['Xstabiliser', 3], ['Xpvc*Xstabiliser', 0, 3]]
[ 0.00182228  0.03291166  0.06479934 -0.54254945 -0.56799642 -0.02459268
 -0.34497569  0.02152983  0.07867065  0.05837493] [['Xpvc', 0], ['Xfiller', 1], ['Xstabiliser', 3], ['Xfiller*Xstabiliser', 1, 3]]
[ 0.06678056  0.12490007  0.15046445 -0.40559249 -1.71175712  0.06526617
 -0.45052955  0.03055333  0.16047471  0.18841869] [['Xpvc', 0], ['Xfiller', 1], ['Xstabiliser', 3], ['Xpvc*Xfiller', 0, 1], ['Xpvc*Xstabiliser', 0, 3]]
[ 0.04700532  0.047694    0.05590712 -0.52312806 -0.47772037  0.04685349
 -0.53714503  0.01305843  0.11143484  0.11125061] [['Xpvc', 0], ['Xfiller', 1], ['Xstabiliser', 3], ['Xpvc*Xfiller', 0, 1], ['Xfiller*Xstabiliser', 1, 3]]
[ 0.0826904   0.1168263   0.10783689 -0.40836947 -1.31097467  0.04207257
 -0.42547506  0.07612801  0.12780164  0.20053278] [['Xpvc', 0], ['Xfi

[-1.47490191  0.12983655  0.12330344 -0.03271351 -0.18336401 -0.05319964
 -0.14772639  0.15403877 -0.02122398  0.19259899] [['Xpvc', 0], ['Xfr', 2], ['Xldh', 5], ['Xpvc*Xldh', 0, 5]]
[ 0.03406847  0.10149564  0.05499371 -0.16252015 -0.26309342  0.03712572
 -0.16787188  0.06437668 -0.02769649  0.12712701] [['Xpvc', 0], ['Xfr', 2], ['Xldh', 5], ['Xfr*Xldh', 2, 5]]
[-2.05833913  0.17512119  0.17191867  0.03167386 -0.28243491 -0.04266768
 -0.09280432  0.1787675  -0.01020233  0.123871  ] [['Xpvc', 0], ['Xfr', 2], ['Xldh', 5], ['Xpvc*Xfr', 0, 2], ['Xpvc*Xldh', 0, 5]]
[ 0.01623157  0.07722659  0.04458542 -0.15657336 -0.2889323   0.00526683
 -0.29793885  0.00464256 -0.04426985  0.02098344] [['Xpvc', 0], ['Xfr', 2], ['Xldh', 5], ['Xpvc*Xfr', 0, 2], ['Xfr*Xldh', 2, 5]]
[-1.46757914  0.10690172  0.08487215 -0.12441567 -0.16326488 -0.05222932
 -0.16334863  0.01539315 -0.01610255  0.19973331] [['Xpvc', 0], ['Xfr', 2], ['Xldh', 5], ['Xpvc*Xldh', 0, 5], ['Xfr*Xldh', 2, 5]]
[-2.04536587  0.16384774  0

[-0.39393534  0.62880685  0.64482469  0.40230271  0.08558089  0.22963021
  0.40674302  0.72298216  0.56950728  0.40427083] [['Xpvc', 0], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xldh', 0, 5], ['Xdinp*Xldh', 4, 5]]
[-0.54089178  0.61042329  0.64255137  0.39724071  0.01352388  0.22709536
  0.29805903  0.67634553  0.56409166  0.38926304] [['Xpvc', 0], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xdinp', 0, 4], ['Xpvc*Xldh', 0, 5], ['Xdinp*Xldh', 4, 5]]
[ 0.15213319  0.17577296  0.17252    -0.10398747 -1.66834499  0.24799885
 -0.63609488  0.20577798  0.11790181  0.21468651] [['Xpvc', 0], ['Xdinp', 4], ['Xsph', 6]]
[ 0.17624461  0.19018918  0.18052674 -0.07086357 -2.14564192  0.26534643
 -0.93653625  0.22958847  0.13221088  0.24101765] [['Xpvc', 0], ['Xdinp', 4], ['Xsph', 6], ['Xpvc*Xdinp', 0, 4]]
[ 0.11490265  0.17050021  0.18033581 -0.14847129 -1.70098659  0.26094202
 -0.66744162  0.1921753   0.09687282  0.21468864] [['Xpvc', 0], ['Xdinp', 4], ['Xsph', 6], ['Xpvc*Xsph', 0, 6]]
[ 0.034358    0.07609644  0.1

[-0.08367162 -0.21908752 -0.09221456 -0.14728797 -2.07674757 -0.13890037
 -0.83432211  0.01234187 -0.34953373 -0.4344753 ] [['Xfiller', 1], ['Xfr', 2], ['Xsph', 6], ['Xfiller*Xfr', 1, 2], ['Xfiller*Xsph', 1, 6]]
[-0.26611586 -0.13807219 -0.03732999 -0.1876902  -1.68264527 -0.2045505
 -0.35485585  0.15791862 -0.3033166  -0.34466616] [['Xfiller', 1], ['Xfr', 2], ['Xsph', 6], ['Xfiller*Xfr', 1, 2], ['Xfr*Xsph', 2, 6]]
[-0.27084441 -0.13601927  0.06032708 -0.23453758 -1.15631054 -0.24475148
 -0.46936038  0.04791203 -0.34755001 -0.48532035] [['Xfiller', 1], ['Xfr', 2], ['Xsph', 6], ['Xfiller*Xsph', 1, 6], ['Xfr*Xsph', 2, 6]]
[-0.3282593  -0.16249348 -0.04640531 -0.19650557 -1.82626928 -0.24359656
 -0.64443926  0.09345252 -0.30653138 -0.41225102] [['Xfiller', 1], ['Xfr', 2], ['Xsph', 6], ['Xfiller*Xfr', 1, 2], ['Xfiller*Xsph', 1, 6], ['Xfr*Xsph', 2, 6]]
[-0.10170967  0.03104789 -0.08223194 -0.99061483 -1.96146047 -0.44212477
 -1.41506141 -0.03258702  0.08347359 -0.46359526] [['Xfiller', 1], 

...

[ 0.03248055  0.26412716  0.405224    0.09327972 -1.12622911  0.08412974
 -0.2933253   0.53879515  0.10912866 -0.30163359] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xfr', 0, 2], ['Xpvc*Xdinp', 0, 4], ['Xfr*Xstabiliser', 2, 3], ['Xfr*Xdinp', 2, 4], ['Xstabiliser*Xldh', 3, 5]]
[ 0.17838208  0.56553564  0.58055757  0.20910284 -0.11145704  0.19391095
  0.26364756  0.58592252  0.40849791 -0.70939294] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xfr', 0, 2], ['Xpvc*Xdinp', 0, 4], ['Xfr*Xstabiliser', 2, 3], ['Xfr*Xdinp', 2, 4], ['Xdinp*Xldh', 4, 5]]
[ 0.34845635  0.1901841   0.31689594 -0.31033603 -1.65453592 -0.21558192
 -1.58605374  0.23892542 -0.00950667  0.40937427] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xfr', 0, 2], ['Xpvc*Xdinp', 0, 4], ['Xfr*Xstabiliser', 2, 3], ['Xfr*Xldh', 2, 5], ['Xstabiliser*Xdinp', 3, 4]]
[ 0.04988795  0.48429578  0.63444426  0.03858194 -1.0339341   0.

[-0.30242658  0.40963056  0.58300591  0.15110712 -0.93993176  0.16557602
  0.40055918  0.52974412  0.38795719 -0.15664281] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xfr', 0, 2], ['Xpvc*Xldh', 0, 5], ['Xfr*Xdinp', 2, 4], ['Xfr*Xldh', 2, 5], ['Xdinp*Xldh', 4, 5]]
[-1.00014861e+00  1.98473301e-01  2.58306185e-01  4.71576227e-03
 -1.73752791e+00  1.45246743e-01 -1.08012515e-01  3.08541661e-01
 -7.16725340e-03 -4.91750946e+00] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xfr', 0, 2], ['Xpvc*Xldh', 0, 5], ['Xfr*Xdinp', 2, 4], ['Xstabiliser*Xdinp', 3, 4], ['Xstabiliser*Xldh', 3, 5]]
[-0.29855633  0.53706499  0.57645904  0.13643862 -0.70887058  0.19593666
  0.40208979  0.60908063  0.23034854 -0.19823333] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xfr', 0, 2], ['Xpvc*Xldh', 0, 5], ['Xfr*Xdinp', 2, 4], ['Xstabiliser*Xdinp', 3, 4], ['Xdinp*Xldh', 4, 5]]
[-0.04303177  0.59655261  0.6294673

[-0.81379356  0.18151137  0.37650877  0.00686763 -1.63673907 -0.06936121
 -0.30594913  0.48634064  0.1604748  -3.3883381 ] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xstabiliser', 0, 3], ['Xpvc*Xdinp', 0, 4], ['Xpvc*Xldh', 0, 5], ['Xfr*Xdinp', 2, 4], ['Xstabiliser*Xldh', 3, 5]]
[-0.29230541  0.50266383  0.57562478  0.01303908 -0.01515521  0.09118003
  0.21154088  0.59113817  0.399924   -0.32204569] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xstabiliser', 0, 3], ['Xpvc*Xdinp', 0, 4], ['Xpvc*Xldh', 0, 5], ['Xfr*Xdinp', 2, 4], ['Xdinp*Xldh', 4, 5]]
[-1.74016211e+00  3.45572478e-01  4.46907433e-01 -2.94076533e-01
 -9.32764730e-01  8.45201380e-04 -8.35208786e-01  3.39045615e-01
  1.05095485e-01  3.59782562e-01] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xstabiliser', 0, 3], ['Xpvc*Xdinp', 0, 4], ['Xpvc*Xldh', 0, 5], ['Xfr*Xldh', 2, 5], ['Xstabiliser*Xdinp', 3, 4]]
[-0.72160686  0.4

  0.40748295  0.63956667  0.40863512 -0.15109601] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xstabiliser', 0, 3], ['Xpvc*Xldh', 0, 5], ['Xfr*Xstabiliser', 2, 3], ['Xfr*Xdinp', 2, 4], ['Xdinp*Xldh', 4, 5]]
[-1.67250563  0.38106503  0.50711269 -0.10415487 -0.51205618  0.13034804
 -0.24119788  0.45201428  0.16372276  0.38546517] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xstabiliser', 0, 3], ['Xpvc*Xldh', 0, 5], ['Xfr*Xstabiliser', 2, 3], ['Xfr*Xldh', 2, 5], ['Xstabiliser*Xdinp', 3, 4]]
[-0.2960048   0.61054444  0.59967724  0.02654987 -0.72479171  0.01152156
 -0.12112253  0.39700693  0.11274316 -2.93678009] [['Xpvc', 0], ['Xfr', 2], ['Xstabiliser', 3], ['Xdinp', 4], ['Xldh', 5], ['Xpvc*Xstabiliser', 0, 3], ['Xpvc*Xldh', 0, 5], ['Xfr*Xstabiliser', 2, 3], ['Xfr*Xldh', 2, 5], ['Xstabiliser*Xldh', 3, 5]]
[-0.35191622  0.34580319  0.52474945  0.21164233  0.08753054  0.19967306
  0.37396562  0.69246483  0.52009812 -0.0091

KeyboardInterrupt: 

In [ ]:
df = pd.DataFrame(total_subset)
df.to_csv("Toatal_model_subset_"  + response + ".csv")

dff = pd.DataFrame(model_subset)
dff.to_csv("limited_model_subset_"  + response + ".csv")

In [ ]:
# plt.plot(CN_hist, AIC_hist, 'r*')
# plt.axis([0, 2000, 12, 20])
# plt.xlabel('CN')
# plt.ylabel('AIC')
# plt.show()

In [ ]:
# plt.plot(VIF_max_hist, AIC_hist1, 'r*')
# plt.show()

In [ ]:
# plt.scatter(CN_hist1, AIC_hist1, c = VIF_max_hist, vmin=0, vmax=50)
# # plt.axis([0, 1000, 12, 20])
# plt.xlabel('CN')
# plt.ylabel('AIC')
# plt.colorbar()
# # plt.set_label('VIF')
# plt.show()

In [ ]:
# from mpl_toolkits.mplot3d import Axes3D

# fig = plt.figure()
# ax = Axes3D(fig)

# ax.scatter(CN_hist1,VIF_max_hist, AIC_hist1)
# plt.xlabel('CN')
# plt.ylabel('VIF')
# ax.set_zlabel('AIC')
# # plt.axis([0, 1000, 12, 18])
# # plt.colorbar()
# plt.show()

In [ ]:
# len(model_subset)

In [ ]:
# for i in model_subset:
#     if i[2] < 550 and i[2] > 450:
#         a = []
#         for j in i[0]:
#             a.append(j[0])
#         print('----model:', a, 'AIC', round(i[1], 3), 'CN:', round(i[2], 3), 'vif_max:', round(i[3], 3), 'R2:', round(i[4], 3), '----'
#              )
        

# 